In [1]:
import yfinance as yf
import numpy as np
import pandas as pd
import tensorflow as tf
from tensorflow.keras.layers import LSTM, Flatten, Dense
from tensorflow.keras.models import Sequential
import tensorflow.keras.backend as K
from tensorflow.keras.layers.experimental import preprocessing

from risk_model import Model
from datetime import datetime

import plotly.graph_objects as go
from pandas_datareader import data as pdr
%matplotlib inline

from absl import logging
tf.get_logger().setLevel('ERROR')

float_formatter = "{:.4f}".format
np.set_printoptions(formatter={'float_kind':float_formatter})
tf.random.set_seed(123)

np.random.seed(123)
yf.pdr_override()  # <== that's all it takes :-)


very_small_float = 1.0 #0.000000001

2022-09-09 07:46:05.980176: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-09-09 07:46:05.980223: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.


In [2]:
from bt_testcode import backtest, DynRebalance, get_name, plotAllocation, getStatistic, calc_portfolio_values
from bt_testcode import plotPortfolioReturns, get_portfolio_values

# Test Model

In [3]:
ticker = """AXISBANK.NS	BPCL.NS	BRITANNIA.NS	CIPLA.NS	DRREDDY.NS	EICHERMOT.NS	GAIL.NS	HDFCBANK.NS	HINDALCO.NS	HINDUNILVR.NS	INFY.NS	IOC.NS	ITC.NS	M&M.NS	MARICO.NS	ONGC.NS	RELIANCE.NS	SAIL.NS	SBIN.NS	SIEMENS.NS	SUNPHARMA.NS	TATACONSUM.NS	TATAMOTORS.NS	TATAPOWER.NS	TATASTEEL.NS	TITAN.NS VEDL.NS	WIPRO.NS""".split()
benchmark_index = "^BSESN"
history_range = {'start': datetime(2000, 1, 1), 
                 'end': datetime(2022, 9, 30)}

stock = pdr.DataReader(ticker, 
                start=history_range['start'],
                end=history_range['end'],
                data_source='yahoo')

[*********************100%***********************]  28 of 28 completed


In [4]:
stock_close = stock.iloc[:125]['Close'].reset_index(drop=True).fillna(very_small_float)
stock_close.head()

AXISBANK.NS    BPCL.NS  BRITANNIA.NS    CIPLA.NS  DRREDDY.NS  EICHERMOT.NS  \
0         5.18  33.270832     75.690002  116.587997  377.062500         4.885   
1         5.38  30.875000     75.455002  117.220001  407.237488         5.140   
2         5.24  29.995832     73.529999  114.804001  392.012512         5.555   
3         5.11  31.691666     78.565002  108.468002  415.387512         6.000   
4         4.86  31.654165     84.849998   99.804001  382.274994         6.465   

    GAIL.NS  HDFCBANK.NS  HINDALCO.NS  HINDUNILVR.NS  ...    SBIN.NS  \
0  8.587504    17.000000    73.833130     230.755005  ...  22.988886   
1  8.293754    17.379999    76.633423     228.104996  ...  24.446625   
2  7.900003    16.695000    82.761711     219.990005  ...  23.441774   
3  8.118754    16.830000    89.238976     228.820007  ...  24.625893   
4  7.831253    16.834999    93.196831     241.294998  ...  25.786425   

   SIEMENS.NS  SUNPHARMA.NS  TATACONSUM.NS  TATAMOTORS.NS  TATAPOWER.NS  \
0   54.494999     14.214153      56.450001      41.535931      7.406506   
1   54.654999     14.023603      55.090000      39.897491      7.420981   
2   52.250000     13.531350      52.794998      40.865227      7.565734   
3   53.000000     13.518182      54.560001      42.561157      7.802163   
4   48.779999     12.436851      58.910000      45.972179      7.787688   

   TATASTEEL.NS  TITAN.NS  VEDL.NS    WIPRO.NS  
0      8.559305    7.7850  2.90875  102.157501  
1      8.466666    7.3700  2.86750  110.330627  
2      8.789500    6.9200  2.85000  112.128754  
3      9.446396    7.4750  2.98250  109.959381  
4      9.654133    7.3175  2.91250  101.163757  

[5 rows x 28 columns]

In [5]:
rnd = 8
tf.random.set_seed(rnd)
np.random.seed(rnd)

param={}
param ={'model_params':
    {'model_n':'LSTM',
    'epochs':1000}}

m = Model()
alloc = m.get_allocations(stock_close.values, **param['model_params'])
alloc

2022-09-09 07:46:29.970503: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcuda.so.1'; dlerror: libcuda.so.1: cannot open shared object file: No such file or directory
2022-09-09 07:46:29.985496: W tensorflow/stream_executor/cuda/cuda_driver.cc:269] failed call to cuInit: UNKNOWN ERROR (303)
2022-09-09 07:46:29.985763: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:156] kernel driver does not appear to be running on this host (divyanshu-PC): /proc/driver/nvidia/version does not exist


1/1 [==============================] - 1s 615ms/step


array([0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.5004,
       0.0000, 0.2288, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
       0.2247, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0461,
       0.0000, 0.0000, 0.0000, 0.0000], dtype=float32)

In [6]:
calc_portfolio_values(alloc, stock_close)

portfolio_returns: 0.3696
std: 0.0249
sharpe: 0.1199


In [7]:

n = [0, 200, 250, 300, 350, 400, 500, 700, 1000, 1300]
def getReturnFromAlloc(n):
    r_list = []
    param={}
    param ={'model_params':
        {'model_n':'LSTM',
        'epochs':1000}}
    print('ret, std, sharp')
    for i in n:
        stock_close = stock.iloc[i:i+125]['Close'].reset_index(drop=True).fillna(very_small_float)
        m = Model()
        alloc = m.get_allocations(stock_close.values, **param['model_params'])
        r_list.append((get_portfolio_values(alloc, stock_close)))
        #print(r_list[-1])
    return r_list

rl = getReturnFromAlloc(n)
sharp = []
for r, s, sp in rl:
    print("{:.4f}  {:.4f}  {:.4f}".format(r,s,sp))
    sharp.append(sp)

pd.DataFrame({'LSTM':sharp}).to_csv('lstm_alloc_result.csv')

ret, std, sharp
1/1 [==============================] - 1s 578ms/step
0.3696  0.0249  0.1199
1.0425  0.0424  0.1983
0.4659  0.0347  0.1083
0.2978  0.0231  0.1038
1.2167  0.1072  0.0916
0.4627  0.0486  0.0768
0.8020  0.0331  0.1954
0.1867  0.0073  0.2064
0.6783  0.0230  0.2376
0.4255  0.0160  0.2149


## Back test
Strategy:
We calculate the best assets allocations based on our model and we assue that this allocation will be the same for the next m days. We don't do any prediction of future returns.

# Back test 2008-2010

In [8]:
config_cerebro = {
    'assets': ticker,
    #'assets':['SPY', 'TLT', 'GLD', 'BA', 'SLV', 'WYNN','MO', 'AEE', 'AIG', 'WY'],
    'benchmark': benchmark_index,
    'startd': history_range['start'],
    'endd': history_range['end'],
    'set_coc' : True,
    'set_coo' : False,
    'cash': 100000.0,
    'stocks_df':None,
    'benchmark_df':None
}

params = {
    'DataCounter': 125,
    'RebalanceDay': 22,
    'reserveCash': 1000.0,
    'printlog': 0,
    'benchmarkUse': True,
    'resetModel':False, 
    'resetModelStep':4,
    'model':Model(),
    'model_params':{
        'model_n':'LSTM',
        'collectData':False,
        'epochs':100}
}
d_res = {}
d_stat = {}

config_cerebro['stocks_df'] = pdr.DataReader(config_cerebro['assets'], 
                start=config_cerebro['startd'],
                end=config_cerebro['endd'],
                data_source='yahoo')
config_cerebro['benchmark_df'] = pdr.DataReader(config_cerebro['benchmark'], 
                start=config_cerebro['startd'],
                end=config_cerebro['endd'],
                data_source='yahoo')

[*********************100%***********************]  28 of 28 completed
[*********************100%***********************]  1 of 1 completed


In [9]:
params['model'] = Model()
params['resetModel'] = False

d_stat[get_name(params)], d_res[get_name(params)], ah = backtest(config_cerebro, DynRebalance, m_name=get_name(params), plot=True, **params)
display(d_stat[get_name(params)])
d_res[get_name(params)].plot()

Starting Portfolio Value: 100000.00
1/1 [==============================] - 0s 49ms/step
Final Portfolio Value: 6065792.97


<IPython.core.display.Javascript object>

CAGR  Max_Drawdown  Sharp_Ratio         Value
LSTM  20.016083     55.203261     0.240639  6.065793e+06

<IPython.core.display.Javascript object>

<AxesSubplot:xlabel='data'>

In [10]:
plotAllocation(ah.dropna())

In [11]:
d_res = {}
d_stat = {}

In [12]:
params['model'] = Model()
params['resetModel'] = True


d_stat[get_name(params)], d_res[get_name(params)], ah = backtest(config_cerebro, DynRebalance, m_name=get_name(params), plot=False, **params)
display(d_stat[get_name(params)])
d_res[get_name(params)].plot()

Starting Portfolio Value: 100000.00
1/1 [==============================] - 0s 32ms/step


KeyboardInterrupt: 

In [ ]:
plotAllocation(ah.dropna())

: 

In [ ]:
getStatistic(d_stat).sort_values(by=['Sharp_Ratio'], ascending=False)

: 

In [ ]:
df = plotPortfolioReturns(d_res)

: 

In [ ]:
getStatistic(d_stat).to_csv('Lstm_stat_2008_2010.csv')
df.to_csv('Lstm_drawdown_2008_2010.csv')

: 

# TEST 2011-2017

In [ ]:
config_cerebro = {
    'assets':['MSFT', 'AMD', 'C', 'BA', 'AMZN', 'AAPL','MO', 'AEE', 'AIG', 'WY'],
    'benchmark':'SPY',
    'startd': datetime(2011, 1, 1),
    'endd'  : datetime(2017, 12, 31),
    'set_coc' : True,
    'set_coo' : False,
    'cash': 11000.0,
    'stocks_df':None,
    'benchmark_df':None
}

params = {
    'DataCounter': 125,
    'RebalanceDay': 22,
    'reserveCash': 1000.0,
    'printlog': 0,
    'benchmarkUse': True,
    'resetModel':False, 
    'resetModelStep':4,
    'model':Model(),
    'model_params':{
        'model_n':'LSTM',
        'collectData':False,
        'epochs':100}
}
d_res = {}
d_stat = {}

config_cerebro['stocks_df'] = pdr.DataReader(config_cerebro['assets'], 
                start=config_cerebro['startd'],
                end=config_cerebro['endd'],
                data_source='yahoo')
config_cerebro['benchmark_df'] = pdr.DataReader(config_cerebro['benchmark'], 
                start=config_cerebro['startd'],
                end=config_cerebro['endd'],
                data_source='yahoo')

: 

In [ ]:
params['model'] = Model()
params['resetModel'] = True

d_stat[get_name(params)], d_res[get_name(params)], ah = backtest(config_cerebro, DynRebalance, m_name=get_name(params), plot=False, **params)
display(d_stat[get_name(params)])
d_res[get_name(params)].plot()

: 

In [ ]:
plotAllocation(ah.dropna())

: 

In [ ]:
getStatistic(d_stat).sort_values(by=['Sharp_Ratio'], ascending=False)

: 

In [ ]:
df = plotPortfolioReturns(d_res)

: 

In [ ]:
getStatistic(d_stat).to_csv('Lstm_stat_2011_2017.csv')
df.to_csv('Lstm_drawdown_2011_2017.csv')

: 

# Test 2018-2021

In [ ]:
config_cerebro = {
    'assets':['MSFT', 'AMD', 'C', 'BA', 'AMZN', 'AAPL','MO', 'AEE', 'AIG', 'WY'],
    'benchmark':'SPY',
    'startd': datetime(2018, 1, 1),
    'endd'  : datetime(2021, 12, 31),
    'set_coc' : True,
    'set_coo' : False,
    'cash': 11000.0,
    'stocks_df':None,
    'benchmark_df':None
}

params = {
    'DataCounter': 125,
    'RebalanceDay': 22,
    'reserveCash': 1000.0,
    'printlog': 0,
    'benchmarkUse': True,
    'resetModel':False, 
    'resetModelStep':4,
    'model':Model(),
    'model_params':{
        'model_n':'LSTM',
        'collectData':False,
        'epochs':100}
}
d_res = {}
d_stat = {}

config_cerebro['stocks_df'] = pdr.DataReader(config_cerebro['assets'], 
                start=config_cerebro['startd'],
                end=config_cerebro['endd'],
                data_source='yahoo')
config_cerebro['benchmark_df'] = pdr.DataReader(config_cerebro['benchmark'], 
                start=config_cerebro['startd'],
                end=config_cerebro['endd'],
                data_source='yahoo')

: 

In [ ]:
params['model'] = Model()
params['resetModel'] = True

d_stat[get_name(params)], d_res[get_name(params)], ah = backtest(config_cerebro, DynRebalance, m_name=get_name(params), plot=False, **params)
display(d_stat[get_name(params)])
d_res[get_name(params)].plot()

: 

In [ ]:
plotAllocation(ah.dropna())

: 

In [ ]:
getStatistic(d_stat).sort_values(by=['Sharp_Ratio'], ascending=False)

: 

In [ ]:
df = plotPortfolioReturns(d_res)

: 

In [ ]:
getStatistic(d_stat).to_csv('Lstm_stat_2018_2021.csv')
df.to_csv('Lstm_drawdown_2018_2021.csv')

: 

# TEST 2012-2016

In [ ]:
config_cerebro = {
    'assets':['MSFT', 'AMD', 'C', 'BA', 'AMZN', 'AAPL','MO', 'AEE', 'AIG', 'WY'],
    'benchmark':'SPY',
    'startd': datetime(2012, 1, 1),
    'endd'  : datetime(2016, 12, 31),
    'set_coc' : True,
    'set_coo' : False,
    'cash': 11000.0,
    'stocks_df':None,
    'benchmark_df':None
}

params = {
    'DataCounter': 125,
    'RebalanceDay': 22,
    'reserveCash': 1000.0,
    'printlog': 0,
    'benchmarkUse': True,
    'resetModel':False, 
    'resetModelStep':4,
    'model':Model(),
    'model_params':{
        'model_n':'LSTM',
        'collectData':False,
        'epochs':100}
}
d_res = {}
d_stat = {}

config_cerebro['stocks_df'] = pdr.DataReader(config_cerebro['assets'], 
                start=config_cerebro['startd'],
                end=config_cerebro['endd'],
                data_source='yahoo')
config_cerebro['benchmark_df'] = pdr.DataReader(config_cerebro['benchmark'], 
                start=config_cerebro['startd'],
                end=config_cerebro['endd'],
                data_source='yahoo')

: 

In [ ]:
params['model'] = Model()
params['resetModel'] = True

d_stat[get_name(params)], d_res[get_name(params)], ah = backtest(config_cerebro, DynRebalance, m_name=get_name(params), plot=False, **params)
display(d_stat[get_name(params)])
d_res[get_name(params)].plot()

: 

In [ ]:
plotAllocation(ah.dropna())

: 

In [ ]:
getStatistic(d_stat).sort_values(by=['Sharp_Ratio'], ascending=False)

: 

In [ ]:
df = plotPortfolioReturns(d_res)

: 

In [ ]:
getStatistic(d_stat).to_csv('Lstm_stat_2012_2016.csv')
df.to_csv('Lstm_drawdown_2012_2016.csv')

: 

# 2016-2021 
SPY, TLT, GLD, IYR

In [ ]:
config_cerebro = {
    'assets':['SPY', 'TLT', 'GLD', 'RWO'],
    'benchmark':'SPY',
    'startd': datetime(2016, 1, 1),
    'endd'  : datetime(2021, 12, 31),
    'set_coc' : True,
    'set_coo' : False,
    'cash': 11000.0,
    'stocks_df':None,
    'benchmark_df':None
}

params = {
    'DataCounter': 125,
    'RebalanceDay': 22,
    'reserveCash': 1000.0,
    'printlog': 0,
    'benchmarkUse': True,
    'resetModel':False, 
    'resetModelStep':4,
    'model':Model(),
    'model_params':{
        'model_n':'LSTM',
        'collectData':False,
        'epochs':1000}
}
d_res = {}
d_stat = {}

config_cerebro['stocks_df'] = pdr.DataReader(config_cerebro['assets'], 
                start=config_cerebro['startd'],
                end=config_cerebro['endd'],
                data_source='yahoo')
config_cerebro['benchmark_df'] = pdr.DataReader(config_cerebro['benchmark'], 
                start=config_cerebro['startd'],
                end=config_cerebro['endd'],
                data_source='yahoo')

: 

In [ ]:
params['model'] = Model()
params['resetModel'] = True

d_stat[get_name(params)], d_res[get_name(params)], ah = backtest(config_cerebro, DynRebalance, m_name=get_name(params), plot=False, **params)
display(d_stat[get_name(params)])
d_res[get_name(params)].plot()

: 

In [ ]:
plotAllocation(ah.dropna())

: 

In [ ]:
getStatistic(d_stat).sort_values(by=['Sharp_Ratio'], ascending=False)

: 

In [ ]:
df = plotPortfolioReturns(d_res)

: 

In [ ]:
getStatistic(d_stat).to_csv('Lstm_stat_etf_2016_2021.csv')
df.to_csv('Lstm_drawdown_etf_2016_2021.csv')

: 

: 

: 

: 

: 